# Elemental Maze Codes

## All the implementation, moveGen and all other functions

In [25]:
import heapq
from collections import deque
import time

### Initialize all the states and function

In [26]:
class ElementalMazeSearch:
    def __init__(self, maze, orb_positions):
        self.maze = maze
        self.orb_positions = orb_positions
        self.goal_positions = self.findGoalPostions()

    def findGoalPostions(self):
        goals = {}
        for x in range(len(self.maze)):
            for y in range(len(self.maze[0])):
                if self.maze[x][y] in ['V', 'L', 'M', 'T']:
                    goals[self.maze[x][y]] = (x, y)
        return goals

    def isGoal(self, orb_positions):
        return (orb_positions['F'] == self.goal_positions['V'] and
                orb_positions['W'] == self.goal_positions['L'] and
                orb_positions['E'] == self.goal_positions['M'] and
                orb_positions['A'] == self.goal_positions['T'])

    def moveGen(self, orb_positions):
        new_states = []
        directions = [(0, 1), (1, 0), (0, -1), (-1, 0)]  # Right, Down, Left, Up

        for orb, (x, y) in orb_positions.items():
            for dx, dy in directions:
                new_x, new_y = x + dx, y + dy
                if self.isValidMove(orb_positions, new_x, new_y):
                    new_orb_positions = orb_positions.copy()
                    new_orb_positions[orb] = (new_x, new_y)
                    new_states.append(new_orb_positions)

            # Check for portal teleportation
            if self.maze[x][y] == 'P':
                for px, py in self.findPortals():
                    if (px, py) != (x, y) and self.isValidMove(orb_positions, px, py):
                        new_orb_positions = orb_positions.copy()
                        new_orb_positions[orb] = (px, py)
                        new_states.append(new_orb_positions)

        return new_states

    def isValidMove(self, orb_positions, x, y):
        if not (0 <= x < len(self.maze) and 0 <= y < len(self.maze[0])):
            return False
        if self.maze[x][y] == '#':
            return False
        if (x, y) in orb_positions.values():
            return False
        return True

    def findPortals(self):
        return [(x, y) for x in range(len(self.maze)) for y in range(len(self.maze[0])) if self.maze[x][y] == 'P']

    def visualizePath(self, path):
        print("Solution Path:")
        for i, orb_positions in enumerate(path):
            print(f"Step {i+1}:")
            maze_copy = [row[:] for row in self.maze]
            for orb, pos in orb_positions.items():
                maze_copy[pos[0]][pos[1]] = orb
            for row in maze_copy:
                print("".join(row))
            print("Orb Positions:", orb_positions)
            print()

### Implement BFS

In [27]:
class BFS(ElementalMazeSearch):
    def search(self):
        queue = deque([self.orb_positions])
        visited = set()
        visited.add(str(self.orb_positions))
        parent = {str(self.orb_positions): None}

        while queue:
            current_positions = queue.popleft()

            if self.isGoal(current_positions):
                path = self.reconstructPath(parent, current_positions)
                self.visualizePath(path)
                return path

            for next_positions in self.moveGen(current_positions):
                state_str = str(next_positions)
                if state_str not in visited:
                    queue.append(next_positions)
                    visited.add(state_str)
                    parent[state_str] = current_positions

        print("No solution found using BFS.")
        return None

    def reconstructPath(self, parent, goal_state):
        path = [goal_state]
        while parent[str(path[-1])] is not None:
            path.append(parent[str(path[-1])])
        return list(reversed(path))

### Implement DFS

In [28]:
class DFS(ElementalMazeSearch):
    def search(self):
        stack = [self.orb_positions]
        visited = set()
        visited.add(str(self.orb_positions))
        parent = {str(self.orb_positions): None}

        while stack:
            current_positions = stack.pop()

            if self.isGoal(current_positions):
                path = self.reconstructPath(parent, current_positions)
                self.visualizePath(path)
                return path

            for next_positions in self.moveGen(current_positions):
                state_str = str(next_positions)
                if state_str not in visited:
                    stack.append(next_positions)
                    visited.add(state_str)
                    parent[state_str] = current_positions

        print("No solution found using DFS.")
        return None

    def reconstructPath(self, parent, goal_state):
        path = [goal_state]
        while parent[str(path[-1])] is not None:
            path.append(parent[str(path[-1])])
        return list(reversed(path))

### Implement Best-First Search

In [29]:
class BestFirstSearch(ElementalMazeSearch):
    def heuristic(self, orb_positions):
        dist = 0
        for orb, pos in orb_positions.items():
            if orb == 'F':
                goal = self.goal_positions['V']
            elif orb == 'W':
                goal = self.goal_positions['L']
            elif orb == 'E':
                goal = self.goal_positions['M']
            elif orb == 'A':
                goal = self.goal_positions['T']
            dist += abs(pos[0] - goal[0]) + abs(pos[1] - goal[1])
        return dist

    def search(self):
        pq = [(self.heuristic(self.orb_positions), 0, self.orb_positions)]
        visited = set()
        visited.add(str(self.orb_positions))
        parent = {str(self.orb_positions): None}
        counter = 1

        while pq:
            _, _, current_positions = heapq.heappop(pq)

            if self.isGoal(current_positions):
                path = self.reconstructPath(parent, current_positions)
                self.visualizePath(path)
                return path

            for next_positions in self.moveGen(current_positions):
                state_str = str(next_positions)
                if state_str not in visited:
                    h = self.heuristic(next_positions)
                    heapq.heappush(pq, (h, counter, next_positions))
                    counter += 1
                    visited.add(state_str)
                    parent[state_str] = current_positions

        print("No solution found using Best-First Search.")
        return None

    def reconstructPath(self, parent, goal_state):
        path = [goal_state]
        while parent[str(path[-1])] is not None:
            path.append(parent[str(path[-1])])
        return list(reversed(path))

In [36]:
# Example Maze and Orb Setup
maze = [
    ['#', '#', '#', '#', '#', '#', '#'],
    ['#', '.', '.', '.', '.', 'V', '#'],
    ['#', '.', '#', '#', '#', '.', '#'],
    ['#', '.', '.', 'P', '.', 'L', '#'],
    ['#', '#', '#', '.', '#', '#', '#'],
    ['#', 'M', '.', '.', '.', 'T', '#'],
    ['#', '#', '#', '#', '#', '#', '#']
]

orb_positions = {
    'F': (1, 1),  # Fire orb
    'W': (3, 1),  # Water orb
    'E': (5, 1),  # Earth orb
    'A': (3, 3)   # Air orb
}

In [37]:
print("BFS Search:")
bfs_solver = BFS(maze, orb_positions)
bfs_solver.search()

BFS Search:
Solution Path:
Step 1:
#######
#F...V#
#.###.#
#W.A.L#
###.###
#E...T#
#######
Orb Positions: {'F': (1, 1), 'W': (3, 1), 'E': (5, 1), 'A': (3, 3)}

Step 2:
#######
#.F..V#
#.###.#
#W.A.L#
###.###
#E...T#
#######
Orb Positions: {'F': (1, 2), 'W': (3, 1), 'E': (5, 1), 'A': (3, 3)}

Step 3:
#######
#..F.V#
#.###.#
#W.A.L#
###.###
#E...T#
#######
Orb Positions: {'F': (1, 3), 'W': (3, 1), 'E': (5, 1), 'A': (3, 3)}

Step 4:
#######
#...FV#
#.###.#
#W.A.L#
###.###
#E...T#
#######
Orb Positions: {'F': (1, 4), 'W': (3, 1), 'E': (5, 1), 'A': (3, 3)}

Step 5:
#######
#....F#
#.###.#
#W.A.L#
###.###
#E...T#
#######
Orb Positions: {'F': (1, 5), 'W': (3, 1), 'E': (5, 1), 'A': (3, 3)}

Step 6:
#######
#....F#
#.###.#
#.WA.L#
###.###
#E...T#
#######
Orb Positions: {'F': (1, 5), 'W': (3, 2), 'E': (5, 1), 'A': (3, 3)}

Step 7:
#######
#....F#
#.###.#
#.WP.L#
###A###
#E...T#
#######
Orb Positions: {'F': (1, 5), 'W': (3, 2), 'E': (5, 1), 'A': (4, 3)}

Step 8:
#######
#....F#
#.###.#
#..W.L#
##

[{'F': (1, 1), 'W': (3, 1), 'E': (5, 1), 'A': (3, 3)},
 {'F': (1, 2), 'W': (3, 1), 'E': (5, 1), 'A': (3, 3)},
 {'F': (1, 3), 'W': (3, 1), 'E': (5, 1), 'A': (3, 3)},
 {'F': (1, 4), 'W': (3, 1), 'E': (5, 1), 'A': (3, 3)},
 {'F': (1, 5), 'W': (3, 1), 'E': (5, 1), 'A': (3, 3)},
 {'F': (1, 5), 'W': (3, 2), 'E': (5, 1), 'A': (3, 3)},
 {'F': (1, 5), 'W': (3, 2), 'E': (5, 1), 'A': (4, 3)},
 {'F': (1, 5), 'W': (3, 3), 'E': (5, 1), 'A': (4, 3)},
 {'F': (1, 5), 'W': (3, 4), 'E': (5, 1), 'A': (4, 3)},
 {'F': (1, 5), 'W': (3, 5), 'E': (5, 1), 'A': (4, 3)},
 {'F': (1, 5), 'W': (3, 5), 'E': (5, 1), 'A': (5, 3)},
 {'F': (1, 5), 'W': (3, 5), 'E': (5, 1), 'A': (5, 4)},
 {'F': (1, 5), 'W': (3, 5), 'E': (5, 1), 'A': (5, 5)}]

In [38]:
print("\nDFS Search:")
dfs_solver = DFS(maze, orb_positions)
dfs_solver.search()


DFS Search:
Solution Path:
Step 1:
#######
#F...V#
#.###.#
#W.A.L#
###.###
#E...T#
#######
Orb Positions: {'F': (1, 1), 'W': (3, 1), 'E': (5, 1), 'A': (3, 3)}

Step 2:
#######
#F...V#
#.###.#
#WAP.L#
###.###
#E...T#
#######
Orb Positions: {'F': (1, 1), 'W': (3, 1), 'E': (5, 1), 'A': (3, 2)}

Step 3:
#######
#F...V#
#.###.#
#WAP.L#
###.###
#ME..T#
#######
Orb Positions: {'F': (1, 1), 'W': (3, 1), 'E': (5, 2), 'A': (3, 2)}

Step 4:
#######
#F...V#
#.###.#
#WAP.L#
###.###
#M.E.T#
#######
Orb Positions: {'F': (1, 1), 'W': (3, 1), 'E': (5, 3), 'A': (3, 2)}

Step 5:
#######
#F...V#
#.###.#
#W.A.L#
###.###
#M.E.T#
#######
Orb Positions: {'F': (1, 1), 'W': (3, 1), 'E': (5, 3), 'A': (3, 3)}

Step 6:
#######
#F...V#
#.###.#
#W.P.L#
###A###
#M.E.T#
#######
Orb Positions: {'F': (1, 1), 'W': (3, 1), 'E': (5, 3), 'A': (4, 3)}

Step 7:
#######
#F...V#
#.###.#
#W.P.L#
###A###
#ME..T#
#######
Orb Positions: {'F': (1, 1), 'W': (3, 1), 'E': (5, 2), 'A': (4, 3)}

Step 8:
#######
#F...V#
#.###.#
#W.P.L#
#

[{'F': (1, 1), 'W': (3, 1), 'E': (5, 1), 'A': (3, 3)},
 {'F': (1, 1), 'W': (3, 1), 'E': (5, 1), 'A': (3, 2)},
 {'F': (1, 1), 'W': (3, 1), 'E': (5, 2), 'A': (3, 2)},
 {'F': (1, 1), 'W': (3, 1), 'E': (5, 3), 'A': (3, 2)},
 {'F': (1, 1), 'W': (3, 1), 'E': (5, 3), 'A': (3, 3)},
 {'F': (1, 1), 'W': (3, 1), 'E': (5, 3), 'A': (4, 3)},
 {'F': (1, 1), 'W': (3, 1), 'E': (5, 2), 'A': (4, 3)},
 {'F': (1, 1), 'W': (3, 1), 'E': (5, 2), 'A': (5, 3)},
 {'F': (1, 1), 'W': (3, 1), 'E': (5, 2), 'A': (5, 4)},
 {'F': (1, 1), 'W': (3, 1), 'E': (5, 2), 'A': (5, 5)},
 {'F': (1, 1), 'W': (3, 1), 'E': (5, 1), 'A': (5, 5)},
 {'F': (1, 1), 'W': (2, 1), 'E': (5, 1), 'A': (5, 5)},
 {'F': (1, 1), 'W': (2, 1), 'E': (5, 1), 'A': (5, 4)},
 {'F': (1, 1), 'W': (2, 1), 'E': (5, 1), 'A': (5, 3)},
 {'F': (1, 1), 'W': (2, 1), 'E': (5, 1), 'A': (4, 3)},
 {'F': (1, 2), 'W': (2, 1), 'E': (5, 1), 'A': (4, 3)},
 {'F': (1, 2), 'W': (2, 1), 'E': (5, 1), 'A': (3, 3)},
 {'F': (1, 2), 'W': (2, 1), 'E': (5, 1), 'A': (3, 2)},
 {'F': (1,

In [39]:
print("\nBest-First Search:")
best_first_solver = BestFirstSearch(maze, orb_positions)
best_first_solver.search()


Best-First Search:
Solution Path:
Step 1:
#######
#F...V#
#.###.#
#W.A.L#
###.###
#E...T#
#######
Orb Positions: {'F': (1, 1), 'W': (3, 1), 'E': (5, 1), 'A': (3, 3)}

Step 2:
#######
#.F..V#
#.###.#
#W.A.L#
###.###
#E...T#
#######
Orb Positions: {'F': (1, 2), 'W': (3, 1), 'E': (5, 1), 'A': (3, 3)}

Step 3:
#######
#..F.V#
#.###.#
#W.A.L#
###.###
#E...T#
#######
Orb Positions: {'F': (1, 3), 'W': (3, 1), 'E': (5, 1), 'A': (3, 3)}

Step 4:
#######
#...FV#
#.###.#
#W.A.L#
###.###
#E...T#
#######
Orb Positions: {'F': (1, 4), 'W': (3, 1), 'E': (5, 1), 'A': (3, 3)}

Step 5:
#######
#....F#
#.###.#
#W.A.L#
###.###
#E...T#
#######
Orb Positions: {'F': (1, 5), 'W': (3, 1), 'E': (5, 1), 'A': (3, 3)}

Step 6:
#######
#....F#
#.###.#
#.WA.L#
###.###
#E...T#
#######
Orb Positions: {'F': (1, 5), 'W': (3, 2), 'E': (5, 1), 'A': (3, 3)}

Step 7:
#######
#....F#
#.###.#
#.WP.L#
###A###
#E...T#
#######
Orb Positions: {'F': (1, 5), 'W': (3, 2), 'E': (5, 1), 'A': (4, 3)}

Step 8:
#######
#....F#
#.###.#
#.

[{'F': (1, 1), 'W': (3, 1), 'E': (5, 1), 'A': (3, 3)},
 {'F': (1, 2), 'W': (3, 1), 'E': (5, 1), 'A': (3, 3)},
 {'F': (1, 3), 'W': (3, 1), 'E': (5, 1), 'A': (3, 3)},
 {'F': (1, 4), 'W': (3, 1), 'E': (5, 1), 'A': (3, 3)},
 {'F': (1, 5), 'W': (3, 1), 'E': (5, 1), 'A': (3, 3)},
 {'F': (1, 5), 'W': (3, 2), 'E': (5, 1), 'A': (3, 3)},
 {'F': (1, 5), 'W': (3, 2), 'E': (5, 1), 'A': (4, 3)},
 {'F': (1, 5), 'W': (3, 3), 'E': (5, 1), 'A': (4, 3)},
 {'F': (1, 5), 'W': (3, 4), 'E': (5, 1), 'A': (4, 3)},
 {'F': (1, 5), 'W': (3, 5), 'E': (5, 1), 'A': (4, 3)},
 {'F': (1, 5), 'W': (3, 5), 'E': (5, 1), 'A': (5, 3)},
 {'F': (1, 5), 'W': (3, 5), 'E': (5, 1), 'A': (5, 4)},
 {'F': (1, 5), 'W': (3, 5), 'E': (5, 1), 'A': (5, 5)}]

In [40]:
def comparePerformance(maze, orbPositions):
    algorithms = [
        ("BFS", BFS),
        ("DFS", DFS),
        ("Best-First Search", BestFirstSearch)
    ]
    
    results = []
    
    for name, algoClass in algorithms:
        solver = algoClass(maze, orbPositions)
        start_time = time.time()
        path = solver.search()
        end_time = time.time()
        
        if path:
            results.append({
                "name": name,
                "time": end_time - start_time,
                "path_length": len(path),
                "path": path
            })
        else:
            results.append({
                "name": name,
                "time": end_time - start_time,
                "path_length": None,
                "path": None
            })
    
    return results

def visualize_all_paths(maze, results):
    print("Comparison of All Search Algorithms:")
    for result in results:
        print(f"\n{result['name']}:")
        print(f"Time taken: {result['time']:.6f} seconds")
        print(f"Path length: {result['path_length'] if result['path_length'] else 'No solution found'}")
        
        if result['path']:
            print("Solution Path:")
            for i, orbPositions in enumerate(result['path']):
                print(f"Step {i+1}:")
                maze_copy = [row[:] for row in maze]
                for orb, pos in orbPositions.items():
                    maze_copy[pos[0]][pos[1]] = orb
                for row in maze_copy:
                    print("".join(row))
                print("Orb Positions:", orbPositions)
                print()

In [41]:
# Run the performance comparison
results = comparePerformance(maze, orb_positions)

# Visualize all paths
visualize_all_paths(maze, results)

# Print performance summary
print("\nPerformance Summary:")
for result in results:
    print(f"{result['name']}:")
    print(f"  Time taken: {result['time']:.6f} seconds")
    print(f"  Path length: {result['path_length'] if result['path_length'] else 'No solution found'}")
    print()

Solution Path:
Step 1:
#######
#F...V#
#.###.#
#W.A.L#
###.###
#E...T#
#######
Orb Positions: {'F': (1, 1), 'W': (3, 1), 'E': (5, 1), 'A': (3, 3)}

Step 2:
#######
#.F..V#
#.###.#
#W.A.L#
###.###
#E...T#
#######
Orb Positions: {'F': (1, 2), 'W': (3, 1), 'E': (5, 1), 'A': (3, 3)}

Step 3:
#######
#..F.V#
#.###.#
#W.A.L#
###.###
#E...T#
#######
Orb Positions: {'F': (1, 3), 'W': (3, 1), 'E': (5, 1), 'A': (3, 3)}

Step 4:
#######
#...FV#
#.###.#
#W.A.L#
###.###
#E...T#
#######
Orb Positions: {'F': (1, 4), 'W': (3, 1), 'E': (5, 1), 'A': (3, 3)}

Step 5:
#######
#....F#
#.###.#
#W.A.L#
###.###
#E...T#
#######
Orb Positions: {'F': (1, 5), 'W': (3, 1), 'E': (5, 1), 'A': (3, 3)}

Step 6:
#######
#....F#
#.###.#
#.WA.L#
###.###
#E...T#
#######
Orb Positions: {'F': (1, 5), 'W': (3, 2), 'E': (5, 1), 'A': (3, 3)}

Step 7:
#######
#....F#
#.###.#
#.WP.L#
###A###
#E...T#
#######
Orb Positions: {'F': (1, 5), 'W': (3, 2), 'E': (5, 1), 'A': (4, 3)}

Step 8:
#######
#....F#
#.###.#
#..W.L#
###A###
#E...T